In [1]:
import os
import os.path as osp

import pickle

from blast import *

from src.python.preprocess2 import *

/home/yotamfr/development/prot2vec/virtualenv/lib/python3.6/site-packages/Bio/SearchIO/__init__.py:211: BiopythonExperimentalWarning: Bio.SearchIO is an experimental submodule which may undergo significant changes prior to its future official release.
  BiopythonExperimentalWarning)


In [10]:
def preds_by_attr(hits_per_uid, attr, func=lambda x: x):
    preds = {}
    pbar = tqdm(range(len(hits_per_uid)), desc="sequences processed")
    for uid, hits in hits_per_uid.items():
        pbar.update(1)
        if len(hits) == 0:
            continue
        preds[uid] = {}
        for go, hits in hits.items():
            hs =[getattr(h, attr) for h in hits if h.evalue < 0.001]
            if len(hs) == 0:
                continue
            preds[uid][go] = func(max(hs))
    pbar.close()
    return preds

def load_object(pth):
    with open(pth, 'rb') as f:
        loaded_dist_mat = pickle.load(f)
        assert len(loaded_dist_mat) > 0
    return loaded_dist_mat

In [11]:
pth_to_hsps = "../../Data/cafapi_blast_MFO_hsp_p2v2"
hits_per_uid = load_object(pth_to_hsps)
preds_pident = preds_by_attr(hits_per_uid, "pident", func=lambda x: x/100)
len(hits_per_uid), len(preds_pident)

sequences processed:   0%|          | 2/18313 [00:00<13:07, 23.26it/s]

{'M': [<blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f23cc3d7978>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blast.HSP object at 0x7f238b4b9ba8>, <blas

(18313, 0)

In [4]:
PATH = "../../Data/CAFA_PI/submission"

if not osp.exists(PATH):
    os.makedirs(PATH)

In [5]:
targets_by_sp = {"208963": load_targets("../../Data/CAFA_PI/targetFiles/target.208963.fasta"),
                 "237561": load_targets("../../Data/CAFA_PI/targetFiles/target.237561.fasta")}

len(targets_by_sp["208963"]), len(targets_by_sp["237561"]), sum(map(len, targets_by_sp.values()))

39%

78%

100%
Finished loading 5892 sequences!


36%

54%

79%

99%

100%
Finished loading 12421 sequences!


(5892, 12421, 18313)

In [6]:
def get_go_dict(targets, preds_by_uid):
    go_dict = {}
    for uid in targets.keys():
        if uid not in preds_by_uid:
            continue
        for go, prob in preds_by_uid[uid].items():
            print(go)
            if go not in go_dict:
                go_dict[go] = [(uid, prob)]
            else:
                go_dict[go].append((uid, prob))
    return go_dict            

In [7]:
num_model = 1
group_id = "yotamfr"

for sp in ["208963", "237561"]:
    go_dict = get_go_dict(targets_by_sp[sp], preds_pident)
    for go in go_dict.keys():
        print(go_dict)
        _, go_id = go.split(":")
        lines = ["AUTHOR\t%s\n" % group_id, "MODEL\t%d\n" % model_num, "KEYWORDS\tblast, homology\n"]
        with open(osp.join(PATH, "%s_%d_%d_%s.txt" % (group_id, num_model, sp, go_id)), "w+") as f:
            for uid, prob in go_dict[go]:
                lines.append("%s\t%s\n" % uid, prob)
            lines.append("END")
            f.writelines(lines)

M
S
T
Q
N
I
P
W
Y
R
H
L
A
F
G
D
V
E
C
K
M
Q
H
N
V
S
E
T
K
L
D
F
R
G
Y
I
P
A
C
W
M
S
N
P
T
R
A
D
G
F
E
W
H
Q
V
K
I
C
Y
L
M
K
I
S
T
G
R
Y
L
E
A
H
P
Q
N
V
D
W
F
C
M
S
E
D
K
Y
R
T
I
F
V
L
H
C
A
G
P
Q
W
N
M
A
N
D
L
K
Q
P
S
V
F
G
I
E
R
T
Y
H
W
C
M
S
Q
R
E
L
F
A
I
P
G
V
N
C
D
H
T
W
Y
K
M
L
N
S
W
P
A
K
D
Q
V
E
I
H
G
F
T
R
C
Y
M
T
R
N
V
A
Q
C
S
W
D
P
I
E
K
L
G
F
Y
H
M
Q
D
K
F
E
L
T
S
A
H
Y
G
R
C
I
N
V
W
P
M
I
N
V
L
D
H
E
R
A
G
K
S
C
W
T
P
Q
Y
F
M
K
H
Y
S
A
T
L
P
F
Q
G
E
R
V
C
N
D
W
I
M
K
L
R
S
V
T
Y
A
F
I
G
Q
E
D
H
N
P
W
C
M
N
I
L
F
G
K
T
Q
V
W
E
R
S
A
P
D
H
C
Y
M
A
L
Q
I
S
E
P
G
H
R
D
T
N
V
Y
K
F
W
C
M
S
Y
L
G
W
V
E
D
K
F
H
T
P
Q
A
I
N
R
C
M
R
P
L
K
Q
A
T
Y
S
D
F
V
E
G
I
H
N
M
L
D
T
P
V
F
A
G
K
R
W
I
Q
Y
H
E
S
N
C
M
L
A
Y
V
I
R
P
T
N
F
Q
G
E
S
D
K
H
W
C
M
D
I
V
F
E
Q
L
S
T
G
Y
W
K
A
N
R
C
H
P
M
T
R
A
V
K
P
F
I
Y
S
L
G
C
H
D
E
Q
N
W
M
A
L
V
F
S
I
H
K
R
P
G
T
Y
E
N
Q
D
W
C
X
M
V
R
P
H
L
N
A
F
E
S
T
I
C
Q
K
G
D
Y
W
M
I
R
S
D
A
Q
H
F
K
L
N
E
G
T
V
P
C
Y
W
M
T
N
L
P
K
F
S
A
H
R
Y
W
G
I
V
Q
C
E
D
M


I
S
H
F
R
V
G
T
L
N
E
K
P
Q
Y
C
W
M
G
K
L
T
A
I
V
W
Q
Y
S
F
N
H
D
R
E
P
M
F
L
K
I
E
R
D
S
T
Q
A
P
V
H
N
G
C
Y
W
M
D
E
L
N
T
K
G
S
V
I
F
A
W
P
Q
R
Y
C
M
L
R
F
Y
A
G
I
V
D
H
S
E
N
Q
K
P
W
T
C
M
D
E
N
K
C
P
G
L
W
T
F
A
S
V
Q
I
R
H
Y
M
Q
I
A
R
S
V
L
F
N
P
H
G
T
W
Y
D
K
E
C
M
K
L
G
I
S
T
V
C
E
Q
A
R
P
D
Y
F
N
H
W
M
N
E
F
Q
P
V
R
L
T
G
A
S
I
K
C
D
Y
W
H
M
S
D
E
L
P
T
R
A
H
F
G
K
V
Y
N
Q
I
W
C
X
M
S
D
P
E
K
N
L
G
T
V
Y
A
I
F
R
W
H
Q
C
M
I
Q
G
K
F
A
R
Y
V
D
L
E
T
N
P
H
S
W
C
M
S
C
E
V
L
T
G
R
I
F
D
Q
A
P
K
N
H
Y
W
M
S
A
F
T
P
E
V
L
R
H
D
Q
I
G
W
N
C
Y
K
M
A
R
V
I
N
G
F
L
Y
E
K
P
D
T
H
S
W
Q
C
M
S
D
N
E
L
Q
I
A
H
R
Y
T
K
G
P
F
W
C
V
M
A
T
G
K
I
V
Q
D
E
F
P
R
Y
L
N
S
H
W
C
M
P
F
T
L
H
R
S
A
I
Q
K
N
G
E
V
C
W
Y
D
M
T
R
S
A
E
P
V
L
Q
F
C
H
G
Y
D
K
I
W
N
M
K
L
T
P
E
D
H
Y
A
G
R
I
N
V
S
Q
F
C
W
M
T
S
E
N
P
L
A
R
K
I
D
V
G
H
Y
F
Q
C
W
M
A
T
K
Q
G
D
R
C
V
L
E
I
S
Y
W
N
P
F
H
M
A
S
Y
E
I
L
D
H
P
F
R
Q
T
G
V
N
K
W
C
M
S
N
K
V
R
Q
E
I
T
F
C
L
A
G
Y
P
D
W
H
M
P
L
S
F
A
R
C
G
N
V
T
I
E
Q
D
K
Y
H
W
M
S
D
L


G
R
T
E
Y
N
I
Q
F
W
C
M
S
T
D
P
A
Q
R
V
L
I
Y
E
K
G
N
C
F
W
H
M
T
I
S
A
R
N
V
K
Y
F
P
E
L
H
D
G
C
Q
W
M
A
P
E
T
G
D
L
V
F
N
K
Y
R
C
I
S
Q
H
W
M
L
R
S
T
H
P
G
A
E
K
V
Q
I
N
F
D
W
Y
C
M
D
I
A
L
H
G
W
E
S
K
R
P
F
Q
T
V
N
Y
C
M
K
T
I
R
Q
L
G
C
A
S
E
P
V
N
W
D
Y
F
H
M
S
E
L
R
I
F
A
G
T
P
D
H
N
V
Q
K
Y
C
W
M
N
R
V
I
P
L
D
E
Q
A
T
G
K
C
Y
F
S
H
W
M
N
Q
S
E
C
P
R
F
K
A
V
D
I
L
W
G
T
Y
H
M
T
I
K
L
V
G
A
N
P
E
Y
R
H
W
F
D
S
Q
C
M
S
W
Q
F
K
H
A
L
I
P
V
G
T
Y
E
R
D
C
N
M
T
V
Q
S
K
N
P
D
I
A
E
F
Y
L
G
R
H
W
C
M
S
E
Q
H
A
G
D
V
L
N
K
T
R
I
F
P
Y
W
C
M
I
N
V
Q
T
A
G
S
E
H
L
Y
D
R
K
C
P
F
W
M
N
L
E
K
I
Q
S
H
R
V
A
P
D
T
F
C
G
Y
W
M
S
P
Q
E
T
A
R
H
V
I
G
F
L
N
K
D
Y
C
W
M
A
S
G
P
F
L
D
T
R
Q
I
W
V
Y
N
E
K
H
C
M
S
K
P
A
I
T
L
W
D
H
F
Y
V
Q
E
G
R
N
C
M
E
N
H
Y
R
L
F
S
A
G
D
V
Q
I
P
K
T
C
W
M
A
S
I
L
G
V
N
P
D
Q
T
K
E
R
Y
F
W
H
M
T
L
E
R
Y
I
V
A
Q
H
F
G
C
S
P
K
D
N
W
M
F
N
K
Q
I
T
L
S
A
G
C
E
D
V
R
P
W
Y
H
M
T
F
I
H
V
E
S
A
P
K
L
D
N
G
Y
Q
R
C
M
S
L
I
N
T
K
P
F
Q
A
G
E
D
R
W
V
Y
C
H
M
E
Q
R
S
A
T
I
V
L
K


D
G
T
R
V
E
A
Q
I
H
W
L
S
P
C
N
F
K
Y
M
A
V
S
F
Q
L
W
R
G
N
T
H
K
I
P
E
C
D
Y
M
F
R
L
N
P
V
G
C
S
A
I
W
D
E
T
Q
K
Y
H
M
A
K
Q
D
Y
E
I
L
G
V
S
T
R
H
P
N
F
C
W
X
M
P
R
T
F
E
C
D
I
L
K
G
V
N
Y
S
Q
A
H
W
M
T
R
Q
H
S
F
A
I
V
L
G
P
D
Y
K
C
N
E
W
M
S
D
R
I
V
N
A
L
G
H
F
P
K
T
E
W
C
Y
Q
M
K
N
W
T
S
A
E
I
L
G
P
V
H
R
C
D
Q
F
Y
M
C
V
T
Q
K
D
R
L
S
N
Y
A
G
F
P
E
I
W
H
M
Q
E
S
I
L
V
D
P
F
K
G
A
Y
T
R
W
N
H
C
M
A
S
V
R
I
E
K
G
D
C
L
F
Q
N
P
Y
H
T
W
M
R
Y
S
D
F
T
Q
I
A
G
W
H
L
V
E
P
N
K
C
M
T
V
K
Q
E
I
N
L
G
H
A
R
P
F
D
S
Y
C
W
M
Q
D
L
R
I
V
G
A
H
F
W
T
S
K
E
P
Y
N
M
S
V
E
N
R
L
P
Q
A
D
F
G
I
C
K
T
W
Y
H
M
V
P
A
L
G
R
N
K
S
T
F
D
Y
E
I
C
Q
H
W
M
S
A
D
R
H
P
V
L
E
I
W
Q
G
F
Y
N
K
T
C
M
S
F
Q
A
V
G
L
N
T
D
I
Y
K
R
E
P
H
W
M
K
P
I
F
S
R
G
L
Q
A
V
D
T
Y
N
E
C
H
W
M
K
A
Q
S
V
L
I
E
D
G
R
T
Y
W
C
H
P
N
F
M
Q
G
D
P
V
L
R
N
E
T
S
A
I
Y
F
H
K
W
C
M
I
G
S
L
T
A
R
F
W
V
P
K
D
Q
E
H
N
Y
C
M
Q
K
S
I
Y
V
A
T
G
R
E
P
H
L
F
D
W
N
C
M
Q
V
L
P
S
T
G
R
F
I
A
Y
E
D
K
N
W
C
H
M
S
A
I
D
C
T
G
L
R
Q
W
K
P
E
N
F
V
Y
H
M
K


T
A
V
Q
D
L
I
H
W
N
C
M
N
K
E
I
L
A
V
S
P
R
F
T
Y
Q
D
G
W
H
C
M
T
R
S
L
N
P
A
I
D
G
H
Q
W
V
K
Y
E
F
C
M
E
T
S
N
L
V
R
I
G
K
F
C
D
P
A
H
Q
Y
W
M
K
F
G
I
E
V
P
N
L
A
D
Y
W
T
H
R
S
Q
C
M
T
E
R
L
A
G
K
V
Q
I
D
S
N
P
F
W
H
Y
C
M
I
E
A
D
Y
L
V
G
S
T
W
H
R
Q
P
F
N
C
K
M
G
Q
R
E
W
L
S
F
N
A
K
T
I
H
D
V
C
P
Y
M
S
V
L
H
R
F
Y
T
K
C
I
N
A
P
E
G
Q
D
W
M
S
E
F
I
A
N
R
G
D
T
P
W
V
C
L
Q
Y
K
H
M
Q
R
I
D
S
H
T
G
E
P
L
V
F
A
W
C
N
Y
K
M
K
W
L
C
S
V
G
I
A
Q
P
D
F
N
H
T
E
R
Y
M
I
E
N
L
R
K
G
F
Y
V
P
D
A
T
S
H
C
Q
W
M
S
E
F
Q
T
I
L
D
P
R
G
V
A
W
K
N
H
C
Y
M
L
A
T
S
I
G
R
K
F
V
E
N
D
P
Q
H
W
Y
C
M
S
K
A
N
V
Y
Q
R
P
E
G
H
L
T
I
D
F
W
C
M
V
K
T
Q
R
I
P
G
E
A
D
L
W
C
N
Y
S
H
F
M
D
Q
L
I
K
E
F
A
Y
H
G
P
S
V
T
C
W
R
N
M
R
K
W
Q
C
V
G
F
I
Y
D
E
A
L
P
T
N
S
H
M
T
S
R
K
L
D
E
I
G
V
P
A
N
Q
W
F
Y
C
H
M
S
D
H
L
I
A
G
V
E
T
F
P
K
Q
W
R
N
Y
C
M
T
K
N
I
Q
V
L
F
C
G
R
S
P
A
E
D
W
H
Y
M
S
N
Y
D
I
K
V
L
G
A
R
P
T
H
F
E
C
Q
W
M
R
L
F
S
P
A
T
I
V
Y
N
Q
K
E
D
G
W
H
C
M
S
W
Q
E
K
I
N
A
L
D
R
Y
P
V
G
F
H
T
C
M
V
P
N
S
Y
R
A
H


...

L
V
W
A
E
H
K
Y
S
G
F
N
T
R
I
P
Q
D
C
M
S
H
A
P
E
R
T
G
V
I
D
W
F
Q
N
L
C
K
Y
M
E
D
L
N
V
S
I
G
A
W
Q
Y
R
K
T
F
P
C
H
M
K
V
L
R
C
Q
F
I
W
A
P
G
H
D
T
E
N
S
Y
X
M
E
S
F
N
T
V
R
Q
Y
D
H
A
I
K
G
L
P
W
C
M
A
K
Q
T
I
V
S
D
H
G
L
E
R
Y
F
N
P
W
C
M
N
L
A
T
I
G
Q
F
V
C
K
Y
W
P
E
R
D
S
H
M
Q
S
T
D
A
G
N
P
R
K
H
E
I
F
V
L
C
Y
W
M
S
K
E
F
R
T
P
H
V
N
G
I
D
L
A
Y
Q
C
W
X
M
K
P
E
D
F
R
A
S
T
G
Y
L
I
V
H
N
Q
C
W
M
K
Q
I
A
F
G
L
H
P
T
N
Y
V
D
S
R
E
C
W
M
R
V
I
G
L
T
C
A
S
D
E
Q
K
H
F
P
N
Y
W
M
P
V
L
H
N
R
I
S
D
A
K
E
T
F
Y
Q
G
W
C
M
N
R
E
L
K
S
G
A
T
F
P
V
D
I
Y
H
Q
W
C
M
A
E
K
F
I
H
T
G
L
V
P
D
N
Q
R
W
Y
S
C
M
S
T
L
A
N
E
V
F
R
D
P
Y
H
G
Q
C
I
K
W
M
Q
S
V
T
P
Y
L
K
A
N
E
G
H
D
R
I
W
F
C
M
L
A
V
H
F
D
K
P
G
E
N
Y
S
R
Q
I
C
W
T
M
K
T
E
P
S
V
I
A
D
G
Q
R
N
F
L
Y
H
W
C
M
A
L
D
F
S
R
K
N
T
I
E
Q
V
P
H
Y
C
G
M
S
G
N
Y
K
V
L
P
D
E
T
A
R
I
Q
H
F
W
M
S
K
T
A
E
I
R
Q
F
L
D
H
G
V
P
N
Y
C
W
M
V
R
K
P
S
T
I
G
Y
L
Q
N
E
A
F
W
C
H
D
M
P
C
R
G
L
H
S
I
A
V
E
F
T
Y
K
D
N
Q
W
M
G
H
L
P
A
E
V
R
Y
T
C
N
D
I
S
F
K
Q
W
M


L
R
K
Y
F
T
N
P
D
G
E
V
I
Q
C
H
W
U
M
T
L
V
P
F
K
Q
D
E
G
N
A
I
S
W
Y
R
H
C
M
K
A
F
T
Y
E
R
V
N
P
L
S
Q
G
I
D
H
C
W
M
S
K
P
F
L
N
A
G
D
Q
E
I
R
H
T
V
Y
C
W
M
S
P
Y
I
L
V
R
H
G
A
T
E
Q
F
C
D
K
N
W
M
S
C
P
V
I
E
L
T
Q
R
D
A
G
F
N
W
H
K
Y
M
T
Q
Y
R
G
L
D
K
P
F
W
A
V
I
C
S
E
N
H
M
I
V
T
G
A
F
S
N
K
L
D
Y
E
Q
H
C
W
R
P
M
Y
R
I
G
E
L
A
K
V
T
P
D
Q
H
F
S
C
N
W
M
A
T
L
K
N
Y
G
R
V
E
D
S
I
P
F
H
Q
C
W
M
V
G
H
S
E
T
D
A
I
P
L
Q
R
F
N
K
Y
C
M
P
A
I
Q
S
E
L
D
V
N
G
F
R
K
Y
H
T
C
W
M
F
R
L
N
P
V
G
C
S
A
I
W
D
E
T
Q
K
Y
H
M
S
K
N
Y
H
I
A
V
L
P
G
D
E
T
Q
R
F
C
W
M
S
T
A
E
Q
R
L
N
P
V
G
Y
W
D
F
C
I
K
H
M
K
H
E
I
L
N
V
G
A
C
S
T
Q
P
F
D
Y
R
W
M
K
P
E
D
F
R
A
S
T
G
Y
L
I
V
H
N
Q
C
W
M
P
S
V
A
L
N
R
F
G
T
K
E
D
Y
Q
I
C
H
W
M
P
E
V
Q
T
D
H
A
L
S
K
R
N
F
I
G
Y
C
W
M
T
S
L
P
C
G
Q
E
R
A
D
H
F
I
Y
V
K
N
W
M
F
Y
A
L
E
I
H
V
S
G
R
P
N
W
Q
C
D
T
K
M
K
A
I
L
G
E
R
P
T
H
V
Q
Y
N
W
D
S
F
C
M
K
I
S
L
V
P
F
N
E
A
Y
T
R
D
G
H
Q
W
C
M
N
K
L
E
Q
F
T
D
P
V
Y
S
G
A
R
I
H
C
W
M
K
F
V
S
N
I
G
L
R
A
P
H
Q
E
D
T
Y
W
C
M
A
E


L
V
E
P
F
Q
R
A
T
K
G
S
I
C
H
Y
W
M
K
L
T
I
R
E
F
S
D
Q
W
P
Y
V
N
H
A
G
C
M
I
K
P
R
V
G
F
C
T
H
A
E
N
Q
D
Y
L
S
W
M
Y
T
L
N
W
Q
P
D
S
G
F
A
R
V
E
I
H
C
K
M
R
S
I
V
Q
H
P
E
K
F
A
N
L
T
D
G
W
C
Y
M
A
S
R
G
V
N
K
I
L
Q
D
P
E
Y
T
W
H
F
C
M
T
E
H
S
Y
A
N
K
P
F
D
L
I
C
V
G
R
Q
W
M
K
L
V
H
A
S
G
I
C
D
Q
T
P
N
W
R
E
F
Y
M
I
D
L
Y
F
A
P
T
N
G
H
K
E
R
V
Q
S
W
C
M
K
T
E
V
D
L
R
A
I
Y
N
G
F
H
Q
S
P
M
P
K
T
S
Y
L
N
F
E
A
H
V
R
I
G
D
C
W
Q
M
A
L
K
F
E
D
I
H
P
G
W
Y
V
T
N
S
R
Q
C
M
F
W
R
D
I
T
L
S
V
K
G
P
A
C
E
N
Q
Y
H
M
L
R
S
F
A
K
I
V
C
Y
N
D
Q
E
T
G
W
H
P
M
A
I
P
V
Y
L
W
K
D
G
S
Q
R
E
H
C
T
N
F
M
K
I
A
L
V
F
T
G
C
S
H
P
W
R
D
Q
E
Y
N
M
Q
G
A
K
S
L
R
I
T
C
H
W
N
P
F
E
Y
V
D
M
W
P
S
C
A
R
F
D
G
Q
Y
V
E
L
N
I
K
T
H
M
D
R
I
G
V
L
F
N
P
E
H
A
Q
S
W
C
T
Y
K
M
L
N
Q
D
T
E
R
V
G
S
K
W
H
A
Y
I
P
F
C
M
I
A
T
G
H
V
D
K
L
Q
N
R
P
E
Y
W
F
S
C
X
M
Q
P
V
I
N
A
E
T
R
L
F
G
K
H
Y
S
D
C
W
M
L
E
V
A
T
G
Q
D
P
S
R
K
H
F
Y
I
N
C
W
M
N
Y
K
I
L
V
S
E
G
Q
H
D
F
T
A
R
W
P
C
M
V
L
I
S
G
R
K
A
E
D
F
Y
C
N
P
T
Q
H
W
M
T
Q
F


G
N
V
H
C
W
M
T
K
L
H
Y
V
D
I
S
A
W
G
R
E
N
P
Q
C
F
M
E
T
P
R
S
L
N
V
F
Y
A
I
Q
H
W
G
D
K
C
M
T
K
S
E
L
I
R
A
Q
H
P
V
D
G
F
Y
N
M
A
V
K
I
F
G
T
Q
L
Y
E
R
D
S
P
H
N
C
W
M
T
V
K
Q
L
R
A
F
S
G
E
H
P
I
D
W
N
Y
C
M
Q
H
K
R
S
A
P
F
L
V
G
T
N
D
Y
E
W
I
C
M
G
R
I
S
F
K
A
T
V
L
Q
D
E
N
H
P
W
Y
C
M
T
D
K
Q
S
L
A
P
V
G
N
Y
I
R
W
E
H
F
C
M
T
D
K
I
R
L
Q
G
V
S
E
A
F
H
P
Y
N
C
W
M
I
H
A
Q
S
R
G
L
F
C
T
V
P
D
Y
K
E
W
N
M
N
S
P
A
L
R
G
I
E
K
T
Q
F
V
D
H
W
Y
C
M
D
K
S
A
R
I
T
L
Q
E
G
V
H
P
Y
N
F
W
C
M
T
D
L
A
Q
E
P
W
R
H
V
I
G
N
F
K
Y
S
C
M
S
E
P
R
F
V
H
L
D
Y
I
G
A
K
T
N
C
Q
W
M
S
K
R
V
T
G
L
P
N
E
W
A
Q
I
D
H
F
Y
C
M
T
E
H
S
Y
A
N
K
P
F
D
L
I
C
V
G
R
Q
W
M
K
T
L
G
F
S
D
Y
I
V
A
E
R
P
N
H
Q
C
W
M
W
R
L
P
A
C
V
H
K
T
S
G
F
I
N
Q
Y
E
D
M
K
Q
A
L
R
V
F
G
I
W
S
H
E
D
P
N
T
Y
C
M
L
R
F
Y
A
G
I
V
D
H
S
E
N
Q
K
P
W
T
C
M
K
T
S
L
F
Y
Q
V
A
I
G
H
P
E
D
C
R
N
W
M
S
R
K
D
G
V
L
A
W
N
F
I
H
P
Y
T
Q
C
E
M
Q
I
L
K
V
G
E
Y
P
D
W
C
A
R
T
F
H
N
S
M
L
H
F
A
G
D
T
V
Y
E
I
N
R
S
Q
P
W
K
C
M
A
D
K
Q
L
I
E
G
S
P
V
T
R
H
F


ValueError: not enough values to unpack (expected 2, got 1)